In [9]:
#!pip install autogluon
#!pip install pandas

In [10]:
import pandas as pd
from autogluon.tabular import TabularPredictor
from sklearn.model_selection import TimeSeriesSplit
from sklearn.model_selection import train_test_split
from sklearn.model_selection import train_test_split
from sklearn.model_selection._split import _BaseKFold
import numpy as np
import random

In [11]:
seed_value = 42  # Replace with your desired seed value
random.seed(seed_value)
np.random.seed(seed_value)

In [12]:
x_train_c = pd.read_csv('cleaned_data_quarterly/C/x_train_c.csv')
y_train_c = pd.read_csv('cleaned_data_quarterly/C/train_c.csv')
x_test_c = pd.read_csv('cleaned_data_quarterly/C/x_test_c.csv')

In [13]:
x_train_c_combined = x_train_c.merge(y_train_c, left_on='date_forecast', right_on='time', how='left')
x_train_c_combined['observed'] = x_train_c_combined['calc_year'].isna().astype(int)
train_data_c = x_train_c_combined.drop(['time', 'calc_year', 'calc_month', 'calc_day', 'calc_hour','snow_density:kgm3_Q0','snow_density:kgm3_Q1','snow_density:kgm3_Q2','snow_density:kgm3_Q3','date_forecast','cloud_base_agl:m_Q0','cloud_base_agl:m_Q1','cloud_base_agl:m_Q2','cloud_base_agl:m_Q3'], axis = 1)
x_test_c['observed'] = x_test_c['calc_year'].isna().astype(int)
test_data_c = x_test_c.drop([ 'calc_year', 'calc_month', 'calc_day', 'calc_hour','date_forecast','location'], axis = 1)

In [14]:
pd.set_option('display.max_rows', None)
naninfo = train_data_c.isna().sum()
naninfo

absolute_humidity_2m:gm3_Q0             0
absolute_humidity_2m:gm3_Q1             0
absolute_humidity_2m:gm3_Q2             0
absolute_humidity_2m:gm3_Q3             0
air_density_2m:kgm3_Q0                  0
air_density_2m:kgm3_Q1                  0
air_density_2m:kgm3_Q2                  0
air_density_2m:kgm3_Q3                  0
ceiling_height_agl:m_Q0              5484
ceiling_height_agl:m_Q1              4395
ceiling_height_agl:m_Q2              4396
ceiling_height_agl:m_Q3              4397
clear_sky_energy_1h:J_Q0                0
clear_sky_energy_1h:J_Q1                0
clear_sky_energy_1h:J_Q2                0
clear_sky_energy_1h:J_Q3                0
clear_sky_rad:W_Q0                      0
clear_sky_rad:W_Q1                      0
clear_sky_rad:W_Q2                      0
clear_sky_rad:W_Q3                      0
dew_or_rime:idx_Q0                      0
dew_or_rime:idx_Q1                      0
dew_or_rime:idx_Q2                      0
dew_or_rime:idx_Q3                

# Trying with validation set equal to half of the estimated data


In [15]:
train_data_c.drop(columns= ['index'], inplace= True)

In [16]:

observed = train_data_c[train_data_c['observed'] == 1]
true =observed[observed['forecast_month'].isin([5, 6, 7])]
true

absolute_humidity_2m:gm3_Q0  absolute_humidity_2m:gm3_Q1  \
4442                           3.5                          3.5   
4443                           3.5                          3.5   
4444                           3.6                          3.6   
4445                           3.8                          3.8   
4446                           4.0                          4.1   
4447                           4.3                          4.3   
4448                           4.4                          4.4   
4449                           4.5                          4.4   
4450                           4.2                          4.2   
4451                           3.9                          4.0   
4452                           4.2                          4.2   
4453                           4.4                          4.4   
4454                           4.3                          4.5   
4455                           4.9                          4.8   
4456                           4.8                          4.8   
4457                           4.8                          4.8   
4458                           4.9                          4.9   
4459                           5.0                          5.1   
4460                           5.2                          5.2   
4461                           5.4                          5.4   
4462                           5.5                          5.5   
4463                           5.6                          5.6   
4464                           5.5                          5.4   
4465                           5.3                          5.4   
4466                           5.4                          5.5   
4467                           5.8                          5.8   
4468                           5.8                          5.8   
4469                           5.7                          5.7   
4470                           5.9                          5.8   
4471                           5.8                          5.7   
4472                           5.6                          5.5   
4473                           5.4                          5.4   
4474                           5.1                          5.1   
4475                           5.0                          5.0   
4476                           5.1                          5.1   
4477                           5.3                          5.3   
4478                           5.3                          5.5   
4479                           5.9                          5.8   
4480                           5.6                          5.6   
4481                           5.5                          5.5   
4482                           5.7                          5.8   
4483                           6.1                          6.2   
4484                           6.3                          6.3   
4485                           6.4                          6.4   
4486                           6.4                          6.4   
4487                           6.4                          6.4   
4488                           6.4                          6.4   
4489                           6.3                          6.3   
4490                           6.2                          6.2   
4491                           6.2                          6.2   
4492                           6.1                          6.1   
4493                           6.1                          6.1   
4494                           6.1                          6.1   
4495                           6.1                          6.0   
4496                           6.0                          6.1   
4497                           6.4                          6.4   
4498                           6.5                          6.5   
4499                           6.4                          6.4   
4500                           6.5                    

In [17]:
from sklearn.model_selection import train_test_split

def split_dataset(train_data, date_column='forecast_month', observed_column='observed'):
    """
    Splits the dataset into a training set and a validation set.
    The validation set includes approximately 50% of the estimated data, evenly distributed across months.
    Additionally, it includes about half of the observed data for May, June, and July, if present.
    The training set includes all months, excluding the observed data that is included in the validation set.
    
    :param train_data: The original training dataset as a pandas DataFrame.
    :param date_column: The name of the column that contains the month information.
    :param observed_column: The name of the column that indicates if the data is observed.
    :return: A tuple (training_set, validation_set)
    """
    # Work with a copy to avoid modifying the original DataFrame
    train_data = train_data.copy()
    train_data.sort_values(by='date_forecast', inplace=True)
    
    # Separate observed and estimated data
    estimated_data = train_data[train_data[observed_column] == 0]
    observed_data = train_data[train_data[observed_column] != 0]
    
    # Split the estimated data into training and validation sets
    estimated_train, estimated_val = train_test_split(
        estimated_data, test_size=0.5, random_state=42, stratify=estimated_data[date_column]
    )
    
    # Check if there are any observed data for May, June, and July
    if not observed_data[observed_data[date_column].isin([5, 6, 7])].empty:
        print("hellooo")
        observed_may_june_july = observed_data[observed_data[date_column].isin([5, 6, 7])]
        observed_train_mjj, observed_val_mjj = train_test_split(
            observed_may_june_july, test_size=0.5, random_state=42, stratify=observed_may_june_july[date_column]
        )
    else:
        
        observed_train_mjj = pd.DataFrame()
        observed_val_mjj = pd.DataFrame()
    
    # Combine the estimated and observed May, June, July data for the validation set
    validation_set = pd.concat([estimated_val, observed_val_mjj])
    validation_set.sort_values(by='date_forecast', inplace=True)
    
    # The rest of the observed data (excluding May, June, July) will be added to the training set
    observed_rest = observed_data[~observed_data[date_column].isin([5, 6, 7])]
    
    # Combine all training parts for the final training set
    training_set = pd.concat([estimated_train, observed_train_mjj, observed_rest])
    training_set.sort_values(by='date_forecast', inplace=True)
    
    return training_set, validation_set

# Create a copy of the DataFrame to pass to the function
# train_data_copy = train_data_c.copy()
# train_data_c, val_data_c = split_dataset(train_data_copy, 'forecast_month', 'observed')

# print(len(train_data_c))
# print(len(val_data_c))

In [18]:
# val_data_c

In [19]:
# train_data_c.drop(columns=['date_forecast'],inplace=True)
# val_data_c.drop(columns=['date_forecast'],inplace=True)

In [20]:
predictor_c= TabularPredictor(label ='pv_measurement',eval_metric= 'mean_absolute_error').fit(train_data = train_data_c,verbosity = 2,presets='best_quality', time_limit= 1500)

No path specified. Models will be saved in: "AutogluonModels\ag-20231109_092756\"
Presets specified: ['best_quality']
Stack configuration (auto_stack=True): num_stack_levels=0, num_bag_folds=8, num_bag_sets=20
Beginning AutoGluon training ... Time limit = 1500s
AutoGluon will save models to "AutogluonModels\ag-20231109_092756\"
AutoGluon Version:  0.8.2
Python Version:     3.9.13
Operating System:   Windows
Platform Machine:   AMD64
Platform Version:   10.0.22621
Disk Space Avail:   692.26 GB / 1022.87 GB (67.7%)
Train Data Rows:    21111
Train Data Columns: 185
Label Column: pv_measurement
Preprocessing data ...
AutoGluon infers your prediction problem is: 'regression' (because dtype of label-column == float and label-values can't be converted to int).
	Label info (max, min, mean, stddev): (999.6, -0.0, 95.95556, 179.52312)
	If 'regression' is not the correct problem_type, please manually specify the problem_type parameter during predictor init (You may specify problem_type as one of:

Fitting AutoMLPipelineFeatureGenerator...
	Available Memory:                    2014.46 MB
	Train Data (Original)  Memory Usage: 31.16 MB (1.5% of available memory)
	Inferring data type of each feature based on column values. Set feature_metadata_in to manually specify special dtypes of the features.
	Stage 1 Generators:
		Fitting AsTypeFeatureGenerator...
			Note: Converting 9 features to boolean dtype as they only contain 2 unique values.
	Stage 2 Generators:
		Fitting FillNaFeatureGenerator...
	Stage 3 Generators:
		Fitting IdentityFeatureGenerator...
	Stage 4 Generators:
		Fitting DropUniqueFeatureGenerator...
	Stage 5 Generators:
		Fitting DropDuplicatesFeatureGenerator...
	Useless Original Features (Count: 8): ['elevation:m_Q0', 'elevation:m_Q1', 'elevation:m_Q2', 'elevation:m_Q3', 'snow_drift:idx_Q0', 'snow_drift:idx_Q1', 'snow_drift:idx_Q2', 'snow_drift:idx_Q3']
		These features carry no predictive signal and should be manually investigated.
		This is typically a feature which 

[1000]	valid_set's l1: 21.6901


KeyboardInterrupt: 

In [ ]:
predictor_c.leaderboard(silent=True)

model  score_val  pred_time_val     fit_time  \
0      WeightedEnsemble_L3 -31.162240      14.376106  1354.781825   
1   NeuralNetFastAI_BAG_L2 -31.453003      10.905966  1114.579106   
2        LightGBMXT_BAG_L1 -31.503435       3.853237   241.988032   
3      WeightedEnsemble_L2 -31.503435       3.854236   242.158066   
4     ExtraTreesMSE_BAG_L2 -31.757871      11.837406   963.221879   
5           XGBoost_BAG_L2 -31.917246      10.672405   981.452165   
6   RandomForestMSE_BAG_L2 -31.951825      11.689503  1000.580390   
7          LightGBM_BAG_L2 -32.086834      10.625361   967.236444   
8        LightGBMXT_BAG_L2 -32.373139      10.672569   972.599141   
9          CatBoost_BAG_L2 -32.692435      10.605824  1016.108301   
10         LightGBM_BAG_L1 -33.273268       2.884052   271.530100   
11   NeuralNetTorch_BAG_L2 -33.492952      11.264614  1095.088346   
12         CatBoost_BAG_L1 -33.726822       0.103021   382.329769   
13    ExtraTreesMSE_BAG_L1 -36.889946       1.165368     8.005244   
14  RandomForestMSE_BAG_L1 -37.534293       1.227032    49.397401   
15   KNeighborsDist_BAG_L1 -45.474198       0.631447     0.111521   
16   KNeighborsUnif_BAG_L1 -45.524748       0.659674     0.153041   
17    LightGBMLarge_BAG_L2 -47.112179      10.596343   962.238280   

    pred_time_val_marginal  fit_time_marginal  stack_level  can_infer  \
0                 0.000000           0.199031            3       True   
1                 0.382136         161.063999            2       True   
2                 3.853237         241.988032            1       True   
3                 0.000999           0.170033            2       True   
4                 1.313576           9.706772            2       True   
5                 0.148576          27.937057            2       True   
6                 1.165673          47.065283            2       True   
7                 0.101531          13.721337            2       True   
8                 0.148739          19.084034            2       True   
9                 0.081994          62.593193            2       True   
10                2.884052         271.530100            1       True   
11                0.740784         141.573239            2       True   
12                0.103021         382.329769            1       True   
13                1.165368           8.005244            1       True   
14                1.227032          49.397401            1       True   
15                0.631447           0.111521            1       True   
16                0.659674           0.153041            1       True   
17                0.072513           8.723173            2       True   

    fit_order  
0          18  
1          14  
2           3  
3           8  
4          13  
5          15  
6          11  
7          10  
8           9  
9          12  
10          4  
11         16  
12          6  
13          7  
14          5  
15          2  
16          1  
17         17

In [ ]:
y_pred_c = predictor_c.predict(test_data_c)
y_pred_c=pd.DataFrame(y_pred_c,columns=['pv_measurement'])
y_pred_c #print the DataFrame

pv_measurement
0         -0.542774
1         -0.688995
2         -0.896938
3          1.370289
4         14.306922
..              ...
715       72.532654
716       43.460899
717       13.072128
718        1.831888
719        0.489012

[720 rows x 1 columns]

In [ ]:
import os
output_dir = 'autogluon'

if not os.path.exists(output_dir):
    os.makedirs(output_dir)

# Save the dataframes into the folder
y_pred_c.to_csv(os.path.join(output_dir, 'y_pred_c.csv'))